In [1]:
import os
from langchain.vectorstores import FAISS
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_core.runnables import RunnableParallel
from langchain_core.prompts import format_document
from langchain_core.runnables import RunnableParallel, RunnableLambda, RunnablePassthrough
from langchain_core.messages import AIMessage, HumanMessage, get_buffer_string
from langchain.document_loaders import HuggingFaceDatasetLoader, PyPDFLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.vectorstores import FAISS
from transformers import AutoTokenizer, AutoModelForQuestionAnswering
from transformers import AutoTokenizer, pipeline, Text2TextGenerationPipeline,AutoModelForCausalLM
from langchain import HuggingFacePipeline
from langchain.chains.question_answering import load_qa_chain
from langchain.chains import RetrievalQA
from langchain.prompts import PromptTemplate
MODEL = "llama2"


c:\Users\ayush\OneDrive\Desktop\digilawyer\env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# Data loader

In [2]:
# import os 
extracted_data = []
# for file in os.listdir(path="data/"):
# loader = PyPDFLoader("data/COI...pdf")
# data = loader.load()
# extracted_data+=(data)
# print(data)


In [3]:
# import os 
lawyer_pdf_data = []
# for file in os.listdir(path="data/"):
loader = PyPDFLoader("data/Thinking_Like_a_Lawyer 1.pdf")
data = loader.load()
lawyer_pdf_data+=(data)
print(data)


[Document(page_content='', metadata={'source': 'data/Thinking_Like_a_Lawyer 1.pdf', 'page': 0}), Document(page_content='thinking like a lawyer', metadata={'source': 'data/Thinking_Like_a_Lawyer 1.pdf', 'page': 1}), Document(page_content='', metadata={'source': 'data/Thinking_Like_a_Lawyer 1.pdf', 'page': 2}), Document(page_content='THINKING LIKE A LAWYER\nA NEW INTRODUCTION\nTO LEGAL REASONING\nFrederick Schauer\nHARVARD UNIVERSITY PRESS\nCambridge, Massachusetts\nLondon, England\n2009', metadata={'source': 'data/Thinking_Like_a_Lawyer 1.pdf', 'page': 3}), Document(page_content='Copyright © 2009 by the President and Fellows of Harvard CollegeAll rights reservedPrinted in the United States of AmericaLibrary of Congress Cataloging-in-Publication DataSchauer, Frederick F., 1946–\nThinking like a lawyer : a new introduction to legal reasoning / Frederick Schauer.\np. cm.\nIncludes bibliographical references and index.ISBN 0-674-03270-5 (alk. paper)1. Law—Methodology. I. Title.K212.S325 200

In [4]:
for idx, content in enumerate(lawyer_pdf_data):
    if "IS THERE LEGAL REASONING?" in content.page_content:
        print(idx)
        break

17


In [5]:
lawyer_pdf_data = lawyer_pdf_data[17:]

In [6]:
crcp_pdf_data = []
loader = PyPDFLoader("data/A1908-05_0 2.pdf")
data = loader.load()
crcp_pdf_data+=(data)
print(data)


[Document(page_content='1 \n THE CODE OF CIVIL PROCEDURE, 1908 \n______ \n \nARRANGEMENT OF SECTIONS \n______ \nPRELIMINARY  \nSECTIONS  \n1.  Short title, commencement and extent. \n2. Definitions. \n3. Subordination of Courts. \n4. Savings. \n5. Application of the Code to Revenue Courts. \n6. Pecuniary jurisdiction.  \n7. Provincial Small Cause Courts. \n8. Presidency Small Cause Courts. \nPART I \nSUITS IN GENERAL \nJURISDICTION OF THE COURTS AND  RES JUDICATA  \n9. Courts to try all civil suits unless barred. \n10. Stay of suit. \n11. Res judicata. \n12.  Bar to further suit. \n13. When foreign judgment not conclusive. \n14. Presumption as to foreign judgments. \nPLACE OF SUING \n15. Court in which suits to be instituted. \n16. Suits to be instituted where subject-matter sit uate. \n17. Suits for immovable property situate within jur isdiction of different Courts. \n18. Place of institution of suit where local limits  of jurisdiction of Courts arc uncertain. \n19. Suits for compens

In [7]:
def prepend_to_matched(match):
    return "section \n" + match.group(0)

In [8]:
import re
pattern = re.compile("\d+\w*\.")
for idx, data  in enumerate(crcp_pdf_data[2:7]):
    # print(data.page_content)
    crcp_pdf_data[idx].page_content =  re.sub(pattern,prepend_to_matched, data.page_content)


In [9]:
crcp_pdf_data[:7]

[Document(page_content='3 \n SECTIONS  \nsection \n50. Legal representative. \nPROCEDURE IN EXECUTION \nsection \n51. Powers of Court to enforce execution. \nsection \n52. Enforcement of decree against legal representat ive. \nsection \n53. Liability of ancestral property.  \nsection \n54. Partition of estate or separation of share. \nARREST AND DETENTION \nsection \n55. Arrest and detention. \nsection \n56. Prohibition of arrest or detention of women in execution of decree for money. \nsection \n57. Subsistence-allowance. \nsection \n58. Detention and release. \nsection \n59. Release on ground of illness. \nATTACHMENT  \nsection \n60. Property liable to attachment and sale in execu tion of decree. \nsection \n61. Partial exemption of agricultural produce. \nsection \n62. Seizure of property in dwelling house. \nsection \n63. Property attached in execution of decrees of se veral Courts. \nsection \n64. Private alienation of property after attachment  to be void.  \n \nSALE  \nsection \

In [10]:
import string
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [11]:
extracted_data

[]

In [12]:
s = "hello brpo!!!!!??ds dsd s-++____--??."
s.translate(str.maketrans('', '', string.punctuation))

'hello brpods dsd s'

In [13]:
s

'hello brpo!!!!!??ds dsd s-++____--??.'

In [14]:
coi_pdf_data= []
loader = PyPDFLoader("data/COI...pdf")
data = loader.load()
coi_pdf_data+=(data)
print(data)


[Document(page_content=' \n \n \n THE CONSTITUTION OF INDIA  \n [As on 26th November , 2021 ] \n \n \n  ', metadata={'source': 'data/COI...pdf', 'page': 0}), Document(page_content='2 \n   \nPREFACE  \n \nThis is the fifth   pocket size edition of the Constitution of India in the \ndiglot form. In this edition, the text of the Constitution of India has been \nbrought up -to-date by incorporating therein all the amendments up to the \nConstitution (One Hundred and Fifth Amendment) A ct, 2021. The foot notes \nbelow the text indicate the Constitution Amendment Acts by which such \namendments have been made.  \nThe Constitution (One Hundredth Amendments ) Act, 2015 containing \ndetails of acquired and transferred territories between the Governme nts of \nIndia and Bangladesh has been provided in APPENDIX I.  \nThe Constitution (Application to Jammu and Kashmir) Order, 2019 and \nthe declaration under article 370(3) of the Constitution have been provided \nrespectively in Appendix II and Ap

In [15]:
coi_pdf_data = coi_pdf_data[3:]

In [16]:
coi_pdf_data[:26]

[Document(page_content='4 \n 9. Persons voluntarily acquiring  citizenship of a foreign State not to \nbe citizens.  \n10. Continuance of the rights of citizenship.  \n11. Parliament to regulate the right of citizenship by law.  \nPART III  \nFUNDAMENTAL RIGHTS  \nGeneral  \n12. Definition.  \n13. Laws inconsistent with or in derogation of the fundamental \nrights.  \n Right to Equality  \n14.    Equality before law.  \n15. Prohibition of discrimination on grounds of religion, race, caste, \nsex or place of birth.  \n16. Equality of opportunity in matters of public employment.  \n17. Abolition of Unto uchability.  \n18. Abolition of titles.  \n Right to Freedom  \n19. Protection of certain rights regarding freedom of speech, etc.  \n20. Protection in respect of conviction for offences.  \n21. Protection of life and personal liberty.  \n21A.  Right to education.  \n22. Protection against arrest and detention in certain cases.  \n Right against Exploitation  \n \n23. Prohibition of traff

In [17]:
def prepend_to_matched(match):
    return "article \n" + match.group(0)

In [18]:
import re
pattern = re.compile("\d+\w*\.")
for idx, data  in enumerate(coi_pdf_data[:27]):
    # print(data.page_content)
    # val =
    coi_pdf_data[idx].page_content = (re.sub(pattern, prepend_to_matched, data.page_content))
    # print(val)

In [19]:
def prepend_to_matched(match):
    return "clause \n" + match.group(0)

In [24]:
nagarik_suraksh_pdf = []
loader = PyPDFLoader("data/bharatiya-nagarik-suraksha-sanhita-511325.pdf")
data = loader.load()
nagarik_suraksh_pdf+=(data)
data

[Document(page_content='THE BHARATIYA NAGARIK SURAKSHA SANHITA, 2023\n——————\nARRANGEMENT  OF  CLAUSES\n——————\nCHAPTER  I\nPRELIMINARY\nCLAUSES\n1. Short title, extent and commencement.2. Definitions.3. Construction of references.4. Trial of offences under Bharatiya Nyaya Sanhita, 2023 and other laws.5. Saving.\nCHAPTER  II\nC\nONSTITUTION  OF CRIMINAL  COURTS  AND OFFICES\n6. Classes of Criminal Courts.\n7. Territorial divisions.\n8. Court of Session.\n9. Courts of Judicial Magistrates.\n10. Chief Judicial Magistrate and Additional Chief Judicial Magistrate, etc.\n11. Special Judicial Magistrates.\n12. Local Jurisdiction of Judicial Magistrates.13. Subordination of Judicial Magistrates.\n14. Executive Magistrates.\n15. Special Executive Magistrates.16. Local Jurisdiction of Executive Magistrates.\n17. Subordination of Executive Magistrates.\n18. Public Prosecutors.19. Assistant Public Prosecutors.\n20. Directorate of Prosecution.\nCHAPTER  III\nP\nOWER  OF COURTS\n21. Courts by which

In [26]:
nagarik_suraksh_pdf[:17]

[Document(page_content='THE BHARATIYA NAGARIK SURAKSHA SANHITA, 2023\n——————\nARRANGEMENT  OF  CLAUSES\n——————\nCHAPTER  I\nPRELIMINARY\nCLAUSES\n1. Short title, extent and commencement.2. Definitions.3. Construction of references.4. Trial of offences under Bharatiya Nyaya Sanhita, 2023 and other laws.5. Saving.\nCHAPTER  II\nC\nONSTITUTION  OF CRIMINAL  COURTS  AND OFFICES\n6. Classes of Criminal Courts.\n7. Territorial divisions.\n8. Court of Session.\n9. Courts of Judicial Magistrates.\n10. Chief Judicial Magistrate and Additional Chief Judicial Magistrate, etc.\n11. Special Judicial Magistrates.\n12. Local Jurisdiction of Judicial Magistrates.13. Subordination of Judicial Magistrates.\n14. Executive Magistrates.\n15. Special Executive Magistrates.16. Local Jurisdiction of Executive Magistrates.\n17. Subordination of Executive Magistrates.\n18. Public Prosecutors.19. Assistant Public Prosecutors.\n20. Directorate of Prosecution.\nCHAPTER  III\nP\nOWER  OF COURTS\n21. Courts by which

In [27]:
def prepend_to_matched(match):
    return "clause \n" + match.group(0)

In [28]:
import re
pattern = re.compile("\d+\w*\.")
for idx, data  in enumerate(nagarik_suraksh_pdf[:17]):
    # print(data.page_content)
    # val =
    nagarik_suraksh_pdf[idx].page_content = (re.sub(pattern, prepend_to_matched, data.page_content))
    # print(val)

In [30]:
nyaya_sanhita_pdf= []
loader = PyPDFLoader("data/278LS(content).p65 - Bharatiya_Nyaya_Sanhita,_2023.pdf")
data = loader.load()
nyaya_sanhita_pdf+=(data)
data

[Document(page_content='THE BHARATIYA NYAYA SANHITA, 2023\n—————\nARRANGEMENT OF CLAUSES\n—————\nCHAPTER I\nPRELIMINARY\nCLAUSES\n1. Short title, commencement and application.\n2. Definitions.\n3. General Explanations and expressions.\nCHAPTERII\nOFPUNISHMENTS\n4. Punishments.\n5. Commutation of sentence of death or imprisonment for life.\n6. Fractions of terms of punishment.\n7. Sentence may be (in certain cases of imprisonment) wholly or partly rigorous or\nsimple.\n8. Amount of fine, liability in default of payment of fine, etc.\n9. Limit of punishment of offence made up of several offences.\n10. Punishment of person guilty of one of several offences, the judgment stating that it\nis doubtful of which.\n11. Solitary confinement.\n12. Limit of solitary confinement.\n13. Enhanced punishment for certain offences after previous conviction.\nCHAPTERIII\nGENERAL EXCEPTIONS\n14. Act done by a person bound, or by mistake of fact believing himself bound, by law.\n15. Act of Judge when acting

In [31]:
nyaya_sanhita_pdf[:13]

[Document(page_content='THE BHARATIYA NYAYA SANHITA, 2023\n—————\nARRANGEMENT OF CLAUSES\n—————\nCHAPTER I\nPRELIMINARY\nCLAUSES\n1. Short title, commencement and application.\n2. Definitions.\n3. General Explanations and expressions.\nCHAPTERII\nOFPUNISHMENTS\n4. Punishments.\n5. Commutation of sentence of death or imprisonment for life.\n6. Fractions of terms of punishment.\n7. Sentence may be (in certain cases of imprisonment) wholly or partly rigorous or\nsimple.\n8. Amount of fine, liability in default of payment of fine, etc.\n9. Limit of punishment of offence made up of several offences.\n10. Punishment of person guilty of one of several offences, the judgment stating that it\nis doubtful of which.\n11. Solitary confinement.\n12. Limit of solitary confinement.\n13. Enhanced punishment for certain offences after previous conviction.\nCHAPTERIII\nGENERAL EXCEPTIONS\n14. Act done by a person bound, or by mistake of fact believing himself bound, by law.\n15. Act of Judge when acting

In [32]:
import re
pattern = re.compile("\d+\w*\.")
for idx, data  in enumerate(nyaya_sanhita_pdf[:13]):
    # print(data.page_content)
    # val =
    nyaya_sanhita_pdf[idx].page_content = (re.sub(pattern, prepend_to_matched, data.page_content))
    # print(val)

In [33]:
extracted_data += coi_pdf_data
extracted_data+=lawyer_pdf_data
extracted_data+=crcp_pdf_data
extracted_data+=nagarik_suraksh_pdf
extracted_data+=nyaya_sanhita_pdf

In [35]:
import re
CLEANR = re.compile('<.*?>|&([a-z0-9]+|#[0-9]{1,6}|#x[0-9a-f]{1,6});')
WHITE_SPACE = re.compile("\s+")
# for pdf in extracted_data: # lower casing the data 
for idx,doc in enumerate(extracted_data):
    extracted_data[idx].page_content = re.sub(CLEANR, '', doc.page_content.lower())
    extracted_data[idx].page_content = re.sub(WHITE_SPACE, ' ', doc.page_content.lower())
    extracted_data[idx].page_content = doc.page_content.translate(str.maketrans('', '', string.punctuation))
    extracted_data[idx].page_content = re.sub("…", '', doc.page_content)
    

In [36]:
extracted_data

[Document(page_content='4 article 9 persons voluntarily acquiring citizenship of a foreign state not to be citizens article 10 continuance of the rights of citizenship article 11 parliament to regulate the right of citizenship by law part iii fundamental rights general article 12 definition article 13 laws inconsistent with or in derogation of the fundamental rights right to equality article 14 equality before law article 15 prohibition of discrimination on grounds of religion race caste sex or place of birth article 16 equality of opportunity in matters of public employment article 17 abolition of unto uchability article 18 abolition of titles right to freedom article 19 protection of certain rights regarding freedom of speech etc article 20 protection in respect of conviction for offences article 21 protection of life and personal liberty article 21a right to education article 22 protection against arrest and detention in certain cases right against exploitation article 23 prohibitio

In [64]:
s = "a suit against you for……………………………y ou "
s.translate(str.maketrans('', '', string.punctuation))

'a suit against you for……………………………y ou '

In [65]:
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [73]:
p = re.compile("\s+")
data = "djkdsflk d   f  d dkf dk kl df k ld fld fd     fdfdfdf"
re.sub(p, ' ',data)

'djkdsflk d f d dkf dk kl df k ld fld fd fdfdfdf'

In [74]:
import nltk
nltk.download("stopwords")
nltk.download("punkt")

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/shivaditya/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/shivaditya/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [86]:
from nltk.corpus import stopwords
def remove_stopwords(s:str)->str:
    words = s.split(" ")
    filtered_words = []
    for word in words:
        if word not in stopwords.words():
            filtered_words.append(word)
    return " ".join(filtered_words)

In [87]:
stopwords.words()

['إذ',
 'إذا',
 'إذما',
 'إذن',
 'أف',
 'أقل',
 'أكثر',
 'ألا',
 'إلا',
 'التي',
 'الذي',
 'الذين',
 'اللاتي',
 'اللائي',
 'اللتان',
 'اللتيا',
 'اللتين',
 'اللذان',
 'اللذين',
 'اللواتي',
 'إلى',
 'إليك',
 'إليكم',
 'إليكما',
 'إليكن',
 'أم',
 'أما',
 'أما',
 'إما',
 'أن',
 'إن',
 'إنا',
 'أنا',
 'أنت',
 'أنتم',
 'أنتما',
 'أنتن',
 'إنما',
 'إنه',
 'أنى',
 'أنى',
 'آه',
 'آها',
 'أو',
 'أولاء',
 'أولئك',
 'أوه',
 'آي',
 'أي',
 'أيها',
 'إي',
 'أين',
 'أين',
 'أينما',
 'إيه',
 'بخ',
 'بس',
 'بعد',
 'بعض',
 'بك',
 'بكم',
 'بكم',
 'بكما',
 'بكن',
 'بل',
 'بلى',
 'بما',
 'بماذا',
 'بمن',
 'بنا',
 'به',
 'بها',
 'بهم',
 'بهما',
 'بهن',
 'بي',
 'بين',
 'بيد',
 'تلك',
 'تلكم',
 'تلكما',
 'ته',
 'تي',
 'تين',
 'تينك',
 'ثم',
 'ثمة',
 'حاشا',
 'حبذا',
 'حتى',
 'حيث',
 'حيثما',
 'حين',
 'خلا',
 'دون',
 'ذا',
 'ذات',
 'ذاك',
 'ذان',
 'ذانك',
 'ذلك',
 'ذلكم',
 'ذلكما',
 'ذلكن',
 'ذه',
 'ذو',
 'ذوا',
 'ذواتا',
 'ذواتي',
 'ذي',
 'ذين',
 'ذينك',
 'ريث',
 'سوف',
 'سوى',
 'شتان',
 'عدا',
 'عسى',
 'عل'

In [88]:
from nltk.corpus import stopwords
# for pdf in extracted_data:
for idx, doc in enumerate(extracted_data):
    extracted_data[idx].page_content = remove_stopwords(doc.page_content)

Exception ignored in: <function SeekableUnicodeStreamReader.__del__ at 0x7ffa89c8b940>
Traceback (most recent call last):
  File "/home/shivaditya/Desktop/Digilawyer/env/lib/python3.8/site-packages/nltk/data.py", line 1158, in __del__
    def __del__(self):
KeyboardInterrupt: 


In [4]:
print((extracted_data[0]))

page_content=' 1 chapter 1: introduction to law and legal reasoning law is "man made" it changes over time to accommodate society\'s needs law is made by legislature law is interpreted by courts to determine 1)whether it is "constitutional" 2)who is right or wrong there is a process which must be followed (called "procedural law") i. thomas jefferson : "the study of the law qualifies a man to be us eful to himself, to his neighbors, and to the public." ii. ask several students to give their definition of "law." a. even after years and thousands of do llars, "law" still is not easy to define b. what does law consist of ? law consists of enforceable rule governing relationships among individuals and between individuals and their society. 1. students need to understand . a. the law is a set of general ideas b. when these general ideas are applied, a judge cannot fit a case to suit a rule; he must fit (or find) a rule to suit the unique case at hand. c. the judge must also supply legitimat

In [37]:
# Define the path to the pre-trained model you want to use
modelPath = "mixedbread-ai/mxbai-embed-large-v1"

# Create a dictionary with model configuration options, specifying to use the CPU for computations
model_kwargs = {'device':'cpu'}

# Create a dictionary with encoding options, specifically setting 'normalize_embeddings' to False
encode_kwargs = {'normalize_embeddings': False}

# Initialize an instance of HuggingFaceEmbeddings with the specified parameters
embeddings = HuggingFaceEmbeddings(
    model_name=modelPath,     # Provide the pre-trained model's path
    model_kwargs=model_kwargs, # Pass the model configuration options
    encode_kwargs=encode_kwargs # Pass the encoding options
)

In [31]:
# Define the path to the pre-trained model you want to use
modelPath = "sentence-transformers/all-mpnet-base-v2"

# Create a dictionary with model configuration options, specifying to use the CPU for computations
model_kwargs = {'device':'cpu'}

# Create a dictionary with encoding options, specifically setting 'normalize_embeddings' to False
encode_kwargs = {'normalize_embeddings': False, 'precision':'binary'}

# Initialize an instance of HuggingFaceEmbeddings with the specified parameters
binary_embeddings = HuggingFaceEmbeddings(
    model_name=modelPath,     # Provide the pre-trained model's path
    model_kwargs=model_kwargs, # Pass the model configuration options
    encode_kwargs=encode_kwargs # Pass the encoding options
)

In [38]:
text = "This is a test document."
query_result = embeddings.embed_query(text)
query_result[:3]

[0.11769086867570877, -0.3104265630245209, 0.9282600283622742]

In [66]:
text = "This is a test document."
query_result = embeddings.embed_query(text)
query_result[:3]

[0.39628759026527405, -1.0931020975112915, 0.8704031109809875]

In [ ]:
embeddings. 

In [33]:
text = "This is a test document."
query_result = binary_embeddings.embed_query(text)
query_result[:3]

[-105, 44, 81]

# Splitting text to chunks

In [39]:
text_splitter=RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=50)

In [91]:
docs = []
for data in extracted_data:
    docs+=data

In [92]:
docs

[('page_content',
  '33 part i the union and its territory 1. name and territory of the union. —(1) india, that is bharat, shall be a union of states. 1[(2) the states and the territories thereof shall be as specified in the first schedule.] (3) the territory of india shall comprise — (a) the territories of the states; 2[(b) the union territories specified in the first schedule; and] (c) such other territories as may be acquired. 2. admission or establishment of new states. —parliament may by law admit into the union, or establish, new states on such terms and conditions as it thinks fit. 3[2a. [sikkim to be associated with the union. ].—omitted by the constitution (thirty -sixth amendment ) act, 1975, s. 5 (w.e.f. 26-4-1975).] 3. formation of new states and alteration of areas, boundaries or names of existing states. —parliament may by law — (a) form a new state by separation of territory from any state or by uniting two or more states or parts of states or by uniting any territor y t

In [40]:
db = FAISS.from_documents(extracted_data, embeddings)

In [41]:
db.save_local("digilawyer_db1.3")


In [61]:
retriever = db.as_retriever(search_kwargs = {
    "k":3,
    "threshold":0.5
})

In [62]:
print((retriever.invoke("""I had fight with my wife yesterday, now she is false accusing me to the police, now what should i do, and what kind of legal rights i've""")))

[Document(page_content='233 no 2 summons for settlement of issues o 5 rr1 5 title  t o name description and place of residence  whereas has instituted a suit against you for……………………………y ou are hereby summoned to appear in this court in person or by a pleader duly instruct ed and able to answer all material question relati ng to the suit or who shall be accompanied by some perso n able to answer all such questions on the day of……19  atoclock in the…………noon to answer the claim 1and further you are hereby directed to file on tha t day a written statement of your defence and to produce on the said day all documents in your possession or power upon which you base your defence or claim for setoff or counterclaim and where you rely on any other document whether in your possession or power or not as evidence in support of your defence or claim for setoff or counterclaim you shall enter such documents in a list to be annexed to the writt en statement take note that in default of your appearance

In [44]:
binary_db = FAISS.from_documents(docs, binary_embeddings)

In [45]:
binary_db.save_local("digilawyer_binary_db1.0")

In [9]:
from sentence_transformers import SentenceTransformer
from sentence_transformers.quantization import quantize_embeddings

# 1. Load an embedding model
model = SentenceTransformer("sentence-transformers/all-mpnet-base-v2")

# 2a. Encode some text using "binary" quantization
binary_embeddings = model.encode(
    ["I am driving to the lake.", "It is a beautiful day."],
    # precision="binary",
)

# 2b. or, encode some text without quantization & apply quantization afterwards
embeddings = model.encode(["I am driving to the lake.", "It is a beautiful day."])
binary_embeddings = quantize_embeddings(embeddings, precision="binary")

In [13]:
model.encode(
    text,
    precision="binary",
)


array([-105,   44,   81, -111,   37,   81,  106,  -24,  -81,   82,    0,
        -26,  -71,   -1,  -81,   18,   61,   47,  -19,  104,   47, -123,
         17,  -55,   48,  122,  -16,   89,   24,  124,  -16,    3,    8,
         67,  -95,  -50,   -4,  -12,   99,   76,   11, -121, -128,   87,
       -110,  -80,  -35,   11,  126,   -8,   27,  -86,   68,  -92,  -46,
        -16,   98,  -44, -128,  -60,   36,   13,  104,  -10,   80,   99,
        -27,  107,   83,   97,   64,   24,  -72,  -17,  -76,   17,   -8,
        109,   61,  120, -113, -108,  -70,  -69,    6,   63,  108,  118,
         69, -128,  -25,   71, -105,  -69,   88, -104], dtype=int8)